In [1]:
import numpy as np
from cadCAD.configuration import Experiment
from cadCAD.configuration.utils import config_sim
from cadCAD.configuration import Configuration
from cadCAD.engine import ExecutionMode, ExecutionContext, Executor
import pandas as pd
from cadcadgolem.golem_embassy import Ambassador

import plotly.express as px
import plotly.io as pio
#pio.renderers.default = "jupyterlab"
import seaborn as sns

In [2]:

def p_something(params,
                substep,
                state_history,
                prev_state):
    parameter = params['parameter']
    random_value_1 = parameter
    random_value_2 = np.random.randn() 
    return {'policy_input_1': random_value_1,
            'policy_input_2': random_value_2}


In [3]:


def s_something(params,
                substep,
                state_history,
                prev_state,
                policy_input):
    new_value = policy_input['policy_input_1']
    new_value += policy_input['policy_input_2']
    return ('something', new_value)


In [4]:


partial_state_update_blocks = [
    {
        'policies': {
            'something': p_something

        },
        'variables': {
            'something': s_something
        }
    }
]



In [5]:
from cadCAD import configs
del configs[:]

MONTE_CARLO_RUNS = 100
SIMULATION_TIMESTEPS =200 

sys_params = {
'parameter': np.linspace(0,30,5), #[0.1, 0.2, 0.3],
}



In [6]:
genesis_states = {
    'something': 0
}




In [7]:
sim_config = {
    'N': MONTE_CARLO_RUNS,
    'T': range(SIMULATION_TIMESTEPS),
    'M': sys_params
}



In [8]:
sim_params = config_sim(sim_config)

exp = Experiment()
exp.append_configs(
    sim_configs=sim_params,
    initial_state=genesis_states,
    partial_state_update_blocks=partial_state_update_blocks
)



In [9]:



golem_conf = {
        'NODES': 10, # Number of nodes to utilise from the Golem Network. If you've got a big simulation to run, try pushing this up to 30. Remember you need at least twice as many simulation runs as you have nodes.
        'BUDGET': 10.0, # Maximum amount of crypto you are prepared to spend
        'SUBNET': "community.3", # choose your subnet, currently this is the test network
#        'SUBNET': "devnet-alpha.3",
        'YAGNA_APPKEY':'517fa9720e9f43a7af2325a92b401e3e', # get this from `yagna app-key list`
        'TIMEOUT': 120 # In seconds - you will need to figure this out for your workload. Max currently is 25min, so 25 * 60 seconds
        }


In [10]:

Executor = Ambassador(Executor, golem_conf)
exec_context = ExecutionContext(context=ExecutionMode.single_mode )
simulation = Executor(exec_context=exec_context, configs=configs)
#simulation = Executor(exec_context=local_mode_ctx, configs=configs)




In [11]:
raw_system_events, tensor_field, sessions = simulation.execute()



Initiating Negotiations With Golem Network
Patience you must have.
See your Jupyter server terminal/log for realtime details
This is a good time to go think about what TIMEOUT you set.
If you are not in a hurry, or you just don't know, you can
set it up to 25 minutes.But note, that is 25 minutes per attempt.
A server could stall, and hold you there for 25 minutes,
before you let that workload go and go find another server.
To stop this, you will have to kill your Jupyter Server.
Just Ctrl-c (a few times) at the same place you're watching the logs.



In [12]:
df = pd.DataFrame(raw_system_events)


In [13]:
print(df)


        something  simulation  subset  run  substep  timestep
0        0.000000           0       0    1        0         0
1        0.313453           0       0    1        1         1
2        0.934801           0       0    1        1         2
3        0.788703           0       0    1        1         3
4        0.821548           0       0    1        1         4
...           ...         ...     ...  ...      ...       ...
100495  31.044825           4       4  100        1       196
100496  29.527958           4       4  100        1       197
100497  30.317705           4       4  100        1       198
100498  31.082555           4       4  100        1       199
100499  30.558311           4       4  100        1       200

[100500 rows x 6 columns]


In [15]:
fig =px.scatter(df,
    x='timestep',
    y='something',
    color='subset',
    opacity=0.2
)

fig.show()